In [1]:
import sympy as sp
import minterpy as mp
import numpy as np
from minterpy.pointcloud_utils import *

from mpl_toolkits import mplot3d
%matplotlib inline

from mpl_toolkits.mplot3d import axes3d

import torch
import torchvision
from torchvision import transforms, datasets

import random
import numpy as np
import matplotlib.pyplot as plt

import os
from operator import itemgetter

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

import ot

from sklearn.neighbors import NearestNeighbors

import ripser
import persim
from persim import plot_diagrams

from operator import itemgetter


#do pip installs as follows to use vedo for plotting point clouds
#pip install vedo
#pip install ipyvtklink

import numpy as np
from vedo import *

import matplotlib.pyplot
from mpl_toolkits.mplot3d import Axes3D

In [2]:
def give_centeroid(arr):
    length = arr.shape[0]
    sum_x = np.sum(arr[:, 0])
    sum_y = np.sum(arr[:, 1])
    sum_z = np.sum(arr[:, 2])
    return np.array([[sum_x/length, sum_y/length, sum_z/length]])

In [35]:
def give_next_neighbours_barycenter_indices(batch_x, input_barycenter, remaining_indices, sweep_radsius):
    
  sweep_radsius = 0.2
  #num_neighbours = int(batch_x.shape[0] / no_of_barycenetrs_required)
    
  wasserDistance = []
  distance_cum_index = np.array([])

  for j in remaining_indices:
    
    wassDistance = dist = np.linalg.norm(batch_x[j]-input_barycenter)

    
    distance_cum_index = np.concatenate((distance_cum_index, np.array([wassDistance, j])), axis = 0)
   
  distance_cum_index = distance_cum_index.reshape(int(distance_cum_index.shape[0]/2), 2)
  distance_cum_index = sorted(distance_cum_index, key=itemgetter(0))
  
  distance_cum_index = np.array(distance_cum_index)
  only_distances = distance_cum_index[:,0]
  print(only_distances)
  where_is_it = np.where( only_distances < sweep_radsius ) 
  print('where_is_it', where_is_it)  
  print('where_is_it[0][-1]', where_is_it[0][-1])
  num_neighbours = where_is_it[0][-1] +1
  
  remaining_indices = distance_cum_index[:,1]

  remaining_indices = remaining_indices.astype(int)
  
    
  A = np.array([])
  for i in range(num_neighbours):
    if(i >= distance_cum_index[:,1].shape[0]):
        break
    A = np.concatenate((A, batch_x[int(distance_cum_index[:,1][i])]), axis = 0 )
  
  A = A.reshape(int(A.shape[0]/3) , 3)
  
  #print("The shape of A is ")
  #print(A.shape)
  next_barycenter = give_centeroid(A) 
  
  next_barycenter = np.array(next_barycenter)
  #print(next_barycenter.shape)
  next_barycenter = next_barycenter.reshape(next_barycenter.shape[0]* next_barycenter.shape[1])
  print(next_barycenter)  
  return A, next_barycenter, remaining_indices,num_neighbours


In [36]:
def get_convergent_barycenters(point_cloud, initial_pt):   
    
    #no_neighbours = int(point_cloud.shape[0] / no_of_barycenetrs_required)
    #initiating no of neighbours
    #no_neighbours = 5
    
    #num_neighbours = int(batch_x.shape[0] / no_of_barycenetrs_required)

    
    bary = initial_pt
    rem_indices = np.array(range(0,point_cloud.shape[0]))
    #print("Size of batch : ", point_cloud.shape[0])
    sampled_barycenters = np.array([])
    sampled_barycenters = torch.tensor(sampled_barycenters)
    covered_indices = np.array([])

    for i in range(int(point_cloud.shape[0])):

        if(len(rem_indices) < 2):
            #print("END")
            break

        #print("Iteration number : ", i+1)
        #print("Input barycenter : ")


        old_bary = bary


        print('rem_indices before', rem_indices)
        neighbours, bary, rem_indices, no_neighbours = give_next_neighbours_barycenter_indices(point_cloud, bary, rem_indices)
        print('no_neighbours', no_neighbours)

        wassDistance = np.linalg.norm(old_bary - bary)  

        covered_indices = np.concatenate((covered_indices, rem_indices[:4] ) ,axis = 0)


        print("Tracking distance between new barycenter and previous barycenter : ",wassDistance )
        if(wassDistance < 0.000001):

            unique_covered_indices = np.unique(covered_indices, axis=0)
            sampled_barycenters = torch.cat((sampled_barycenters, torch.tensor(bary)), 0)

            s1 = set(rem_indices)
            s2 = set(unique_covered_indices)
            rem_set = s1 - s2
            rem_inds = list(rem_set)
            #rem_indices = rem_set
            rem_indices = rem_indices[no_neighbours:]

            #print("Sampled barycenters are")
            #print(sampled_barycenters)
            #no_neighbours = 5
            print('rem_indices',rem_indices)
            print("len(rem_indices)",len(rem_indices))
            if(len(rem_indices) ==0):
                break
            bary = point_cloud[rem_indices[0]]
    sampled_barycenters = sampled_barycenters.reshape(int((sampled_barycenters.shape[0]/3)),3)
    
    return sampled_barycenters

In [5]:
def _compute_distance_matrix(x, p=2):
    x_flat = x.view(x.size(0), -1)

    distances = torch.norm(x_flat[:, None] - x_flat, dim=2, p=p)

    return distances

In [6]:
def get_persistence_diagram(point_cloud, maximum_dim):

    point_cloud = torch.tensor(point_cloud)

    dist_matrix = _compute_distance_matrix(point_cloud, p=2)
    diagrams = ripser.ripser(dist_matrix.cpu().detach().numpy(), distance_matrix=True, maxdim=maximum_dim)['dgms']
    return diagrams, plot_diagrams(diagrams, show=True)


# Torus in 3D

In [7]:
x, y, z = sp.symbols('x y z')


In [8]:
## Torus
R = 1.5
r = 0.7
expr_torus = (x**2 + y**2 + z**2 + R**2 - r**2)**2 - 4*R**2*(x**2 + y**2)


In [9]:
expr_torus

-9.0*x**2 - 9.0*y**2 + 3.0976*(0.568181818181818*x**2 + 0.568181818181818*y**2 + 0.568181818181818*z**2 + 1)**2

In [10]:
poly_torus = sp.Poly(expr_torus, x, y, z)

In [11]:
sp.expand(expr_torus)

1.0*x**4 + 2.0*x**2*y**2 + 2.0*x**2*z**2 - 5.48*x**2 + 1.0*y**4 + 2.0*y**2*z**2 - 5.48*y**2 + 1.0*z**4 + 3.52*z**2 + 3.0976

In [12]:
#Convert sympy polynomial to minterpy polynomial

newt_poly_torus = sympy_to_mp(poly_torus, mp.NewtonPolynomial)

# Trials on Torus : 

In [13]:
#Sample points on the zero isocontour
def points_on_torus(num_points):
    
    point_data_torus = sample_points_on_poly(num_points,        # Number of points to be sampled
                                       newt_poly_torus,  # Polynomial in Newton basis
                                       bounds=3.0, # Boundary of the Cubic domain to be sampled
                                       tol=1e-15)  # Tolerance in solution
    
    return point_data_torus

# 1. 1000 barycenters from 10000 points

In [14]:
#Sample points on the zero isocontour

point_data_torus = sample_points_on_poly(1000,        # Number of points to be sampled
                                   newt_poly_torus,  # Polynomial in Newton basis
                                   bounds=3.0, # Boundary of the Cubic domain to be sampled
                                   tol=1e-15)  # Tolerance in solution

In [15]:
point_data_torus.shape

(1000, 3)

In [20]:
x_t = point_data_torus[:,0]
y_t = point_data_torus[:,1]
z_t = point_data_torus[:,2]


plot_points = [x_t,y_t,z_t]
Points(plot_points).show(axes=1)

ViewInteractiveWidget(height=960, layout=Layout(height='auto', width='100%'), width=960)

# demo of barycenter convergence on a torus


In [37]:
torus_bary = get_convergent_barycenters(point_data_torus, point_data_torus[0])

rem_indices before [  0   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17
  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35
  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53
  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71
  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89
  90  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106 107
 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125
 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143
 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161
 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179
 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197
 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215
 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233
 234 235 236 237 238 239 240 241

[0.03636537 0.03636537 0.22089282 0.27250259 0.36851192 0.36870897
 0.37488995 0.37592324 0.38149655 0.41312904 0.41755791 0.43129706
 0.44951832 0.52339519 0.53855947 0.54755266 0.55522829 0.56788336
 0.57846007 0.60072041 0.60332002 0.61628556 0.6286257  0.63306441
 0.63814864 0.63919935 0.65542857 0.6578686  0.66635779 0.66982361
 0.69572333 0.71862926 0.7283096  0.73803324 0.77238384 0.78134454
 0.78760323 0.79368858 0.81924599 0.83059933 0.83138829 0.83544429
 0.83871773 0.83966043 0.85356887 0.86592207 0.86967491 0.87318154
 0.87675975 0.87977098 0.88019819 0.88068094 0.88071507 0.88527013
 0.88966435 0.89772015 0.90437324 0.90558161 0.90784501 0.91254524
 0.91481569 0.91886282 0.93281284 0.94029368 0.94171177 0.95420724
 0.95747138 0.95991753 0.96074427 0.96088823 0.96569148 0.97731
 0.98142256 0.98264327 0.98388105 0.99524608 1.01368582 1.01493354
 1.01732655 1.02010185 1.02133322 1.02322095 1.0241683  1.02619341
 1.02902841 1.03994414 1.04164387 1.04716091 1.0582787  1.0620049

[0.         0.1249317  0.17827119 0.18666318 0.22237007 0.2282889
 0.26792862 0.30948076 0.33885144 0.36516641 0.38493289 0.38885764
 0.40276454 0.40512731 0.41922349 0.46964124 0.5122884  0.53923925
 0.54323995 0.56039734 0.58024837 0.5886711  0.60707844 0.60789699
 0.63069306 0.6319774  0.63398327 0.65055508 0.66701849 0.67224387
 0.68086347 0.69252105 0.69810619 0.7154134  0.72512094 0.75774918
 0.7892334  0.80157402 0.81553202 0.82158298 0.83618833 0.86761548
 0.86849463 0.86950096 0.8750788  0.87888675 0.87912195 0.88087246
 0.9055223  0.91063873 0.91418881 0.91533392 0.92204237 0.94047517
 0.94259306 0.9454266  0.94665701 0.95624081 0.98088008 0.98718869
 0.98748512 0.99092486 1.01021164 1.01217501 1.02011918 1.02465103
 1.02570284 1.03217034 1.05666018 1.05857466 1.0600032  1.06337848
 1.07107634 1.07763784 1.0822687  1.08654729 1.09751672 1.09760111
 1.09778573 1.12065641 1.12605278 1.13543619 1.1354379  1.13929935
 1.14168431 1.15098094 1.15832138 1.15857152 1.17277491 1.17458

 376 159 158 936  45 134 772 939 587 659 743 333  91]
[0.0269291  0.04868896 0.07482696 0.33040322 0.33545017 0.34176278
 0.35701383 0.40580627 0.42973935 0.43553825 0.44806063 0.4641205
 0.47382895 0.53465775 0.54219265 0.56116161 0.56395768 0.58145833
 0.59062382 0.59077836 0.60400819 0.62762581 0.65455293 0.67473547
 0.67917001 0.69059189 0.71592443 0.73264224 0.73435964 0.73702928
 0.74947257 0.76618305 0.77111296 0.77268823 0.79718043 0.79912019
 0.81331827 0.82810463 0.83203178 0.83310855 0.83840406 0.84099029
 0.84125933 0.88652877 0.88838127 0.90251142 0.9040396  0.90656313
 0.91245372 0.92697496 0.93519559 0.94557731 0.94626262 0.95402977
 0.95426741 0.96423065 0.97745043 0.9779934  0.98918654 0.99306515
 1.00017881 1.02835226 1.03051344 1.03134791 1.04329911 1.0516878
 1.05302243 1.07638932 1.08960527 1.10508698 1.10731919 1.11619431
 1.13054759 1.13862033 1.14089007 1.14738268 1.15896523 1.15952721
 1.18211703 1.18433805 1.20302656 1.20828051 1.22225047 1.22345505
 1.2268642

[0.05648443 0.06438904 0.15236594 0.17790291 0.18406916 0.22587836
 0.24415363 0.24696303 0.26110788 0.30497191 0.34406755 0.38344463
 0.41647946 0.44635657 0.45324252 0.46274645 0.47776862 0.50308816
 0.5038112  0.50443847 0.53732548 0.54070704 0.57489237 0.58692351
 0.59317821 0.59581077 0.62287172 0.62510046 0.63827365 0.63967104
 0.67021501 0.67024541 0.67355287 0.69237127 0.69722169 0.70166351
 0.71390914 0.7161675  0.72014808 0.73009375 0.73398429 0.73449564
 0.75023855 0.76258149 0.77418378 0.78169557 0.80311566 0.80448493
 0.81039561 0.815022   0.83338578 0.83785458 0.83934284 0.8418517
 0.84864723 0.85169498 0.85268935 0.86410024 0.86848998 0.87082234
 0.88981899 0.89264867 0.8983009  0.90410715 0.91467023 0.92221435
 0.93257106 0.94599225 0.95022252 0.96336477 0.96452728 0.97522661
 0.97656024 0.98016048 1.0014644  1.02441538 1.0308384  1.03704045
 1.04114388 1.04426717 1.04977068 1.05237597 1.05298212 1.05543546
 1.05569713 1.0566045  1.06339662 1.0683833  1.08119416 1.09684

...

[0.         0.06826362 0.203451   0.20966925 0.27363702 0.28297979
 0.34825217 0.37317329 0.38001589 0.3817007  0.42050649 0.43580825
 0.48829302 0.514224   0.54235055 0.5789806  0.6481669  0.68463079
 0.7471493  0.86662351 0.900125   1.01806032 1.07050667 1.13006906
 1.13794682 1.25720375 1.37745869 1.38447023 1.40383819 1.43335131
 1.45384974 1.46735719 1.47687486 1.48981983 1.49029359 1.4918777
 1.51369376 1.52377674 1.54189547 1.59314819 1.61144673 1.62723229
 1.65823522 1.66223849 1.667371   1.71721929 1.78205414 1.79982131
 1.80360147 1.8663682  1.89249588 1.94396793 1.94835849 1.98117159
 2.00737124 2.04681582 2.06113458 2.10928289 2.13813264 2.13816633
 2.1889481  2.21723977 2.23453316 2.27743413 2.2951441  2.30288129
 2.30606084 2.37146592 2.37388114 2.38654002 2.3896008  2.39422483
 2.41177018 2.43269238 2.43730437 2.44920726 2.45644479 2.46267003
 2.46386039 2.47268591 2.47875736 2.48281984 2.52959737 2.52987284
 2.5325623  2.53936492 2.55227145 2.55509115 2.55561495 2.57709

where_is_it (array([0, 1, 2]),)
where_is_it[0][-1] 2
[ 0.54759035 -1.45323516 -0.69472847]
no_neighbours 3
Tracking distance between new barycenter and previous barycenter :  0.053731979621145946
rem_indices before [268 841 202 120 425 835  79 206 969 777 308 661 108 896 910 588 239 784
 461 602 267 718 317 689 228 937 954 307 716 423 638 510 928  67 819 432
 301 571   5  23 235  61 814 290 266 467 543 719 131 143 708 772 121 244
 134 376 306 686 587  62 405  45 302 684  11 743 555 374 873 237 333 298
  91 767 998 157 939 196 462   1  34 659 598 470 482 702 936 520 261 479
 214 107 159 499 158 978 567 707 690 433 726 546 926  28 636 225 486 852
 893 428 668 781 640 509 114 836  35 923 416 976  27 953 173 406 175 859
 184 994  92 902 541 256 322  22 481 296 693 692 141 600   4 295 927 964
 524 597 622 170 367  55  49  52 560 348 257 783 491 944 167 604 394 699
 728 897 817 252 664 233 147 961 674 804 346 219 422 475 997]
[0.01556263 0.09863732 0.10746396 0.22406232 0.31237302 0.31960205

[0.         0.17148226 0.28204521 0.35865884 0.3875193  0.39974162
 0.40789334 0.41231848 0.46513847 0.50455758 0.68296299 0.98509128
 1.38869    1.44988779 1.47738565 1.49213574 1.50549176 1.53260983
 1.59174311 1.61966459 1.63389384 1.64142589 1.65353929 1.65826867
 1.66148955 1.67576017 1.68201571 1.71828911 1.73274126 1.74169806
 1.78261441 1.80505392 1.80969379 1.8203162  1.8212884  1.85683647
 1.86909855 1.89126022 1.89636777 1.92266858 1.92589754 1.93430064
 1.98469782 1.99139899 1.99372478 2.0341458  2.04823235 2.0623915
 2.07268643 2.13747191 2.19566119 2.20397134 2.22076184 2.22401235
 2.23211382 2.23651536 2.23958195 2.25581197 2.28832862 2.29282298
 2.31973801 2.33809555 2.35118518 2.3728488  2.38023301 2.38140962
 2.3888962  2.39079116 2.41462237 2.45491815 2.46282456 2.48724092
 2.49633192 2.49770542 2.52482279 2.5666369  2.59664349 2.62397108
 2.63119417 2.64157612 2.67482011 2.67864008 2.68439838 2.69348097
 2.72661507 2.73091439 2.73255676 2.75792236 2.76542979 2.77166

rem_indices [600   4 295 184 622 296 491 604 728 699 817 897 233 674 346 252 219 664
 422 804 167 394 147 997 961 475 256 944 783 978 257 348  52  55 560 367
 170 597  49 524 964 927 290 781 173 416  34 859 668 836 470 953 998 405
 432 114 893 976 499 509 196 121 684  28 767 873 157 926 520 462 298 159
 158 702   1 482 936 659 244  62 939  11 686 555 302  91 333 376  45 239
 743 708 143 784 131 461 467 587 134 772]
len(rem_indices) 100
rem_indices before [600   4 295 184 622 296 491 604 728 699 817 897 233 674 346 252 219 664
 422 804 167 394 147 997 961 475 256 944 783 978 257 348  52  55 560 367
 170 597  49 524 964 927 290 781 173 416  34 859 668 836 470 953 998 405
 432 114 893 976 499 509 196 121 684  28 767 873 157 926 520 462 298 159
 158 702   1 482 936 659 244  62 939  11 686 555 302  91 333 376  45 239
 743 708 143 784 131 461 467 587 134 772]
[0.         0.11975181 0.14566258 0.48552669 0.73423337 0.75910007
 0.83212041 0.85104427 0.88816017 0.89385981 0.90254224 0.91621946


rem_indices before [ 45 376 302 555 743 333 772  91 587 134 708  11 686 143 131  62 467 244
 893 470 499  28 509  34 114 668 781 836 953 976 416 173 859 784 239 461]
[0.04767569 0.09005685 0.0914279  0.11994917 0.15183814 0.15239326
 0.24799078 0.26693347 0.35242412 0.39420089 0.63610656 0.64488945
 0.73618997 0.80916201 0.81720204 0.82185909 0.86977863 0.90842305
 1.18807889 1.21596786 1.22323051 1.23268668 1.24881929 1.28537744
 1.30582461 1.34835423 1.40608556 1.44798268 1.48188193 1.50674021
 1.52288069 1.58335857 1.60838946 1.68289617 1.69009672 1.74857294]
where_is_it (array([0, 1, 2, 3, 4, 5]),)
where_is_it[0][-1] 5
[ 1.91815609 -0.9607159  -0.25155747]
no_neighbours 6
Tracking distance between new barycenter and previous barycenter :  0.0
rem_indices [ 91 772 587 134 708  11 686 143  62 131 467 244 893 470 499  28 509  34
 114 668 781 836 953 976 416 173 859 784 239 461]
len(rem_indices) 30
rem_indices before [ 91 772 587 134 708  11 686 143  62 131 467 244 893 470 499  28 509 

In [38]:
torus_bary.shape

torch.Size([344, 3])

In [39]:
# plotting the sampled barycenters

x_stb = torus_bary[:,0]#.cpu().detach().numpy()

y_stb = torus_bary[:,1]#.cpu().detach().numpy()

z_stb = torus_bary[:,2]#.cpu().detach().numpy()



plot_points = [x_stb,y_stb,z_stb]
Points(plot_points).show(axes=1)

ViewInteractiveWidget(height=960, layout=Layout(height='auto', width='100%'), width=960)